In [1]:
from pathlib import Path
from IPython.display import HTML
from collections import defaultdict
import re
import pickle
import matplotlib as mpl
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from PIL import Image
import random

In [2]:

def build_fast_structure(root_dir):
    root = Path(root_dir)
    data = defaultdict(lambda: defaultdict(lambda: {"frames": [], "num_frames": 0}))

    for png_path in root.rglob("*.png"):
        parts = png_path.parts
        class_folder = parts[1]  # "Abuse", "Vandalism"...

        filename = png_path.stem

        video_name, frame_str = filename.split("_x264_")
        frame_num = int(frame_str)

        data[class_folder][video_name]["frames"].append((frame_num, png_path))

    # Sort frames by frame number and store only paths
    for class_name in data:
        for video_name in data[class_name]:
            frames = data[class_name][video_name]["frames"]
            frames_sorted = [p for _, p in sorted(frames)]
            data[class_name][video_name]["frames"] = frames_sorted
            data[class_name][video_name]["num_frames"] = len(frames_sorted)

    return {cls: dict(videos) for cls, videos in data.items()}

train_videos = build_fast_structure("Train")
test_videos  = build_fast_structure("Test")

In [3]:
with open("train_structure.pkl", "wb") as f:
    pickle.dump(train_videos, f, protocol=pickle.HIGHEST_PROTOCOL)
with open("test_structure.pkl", "wb") as f:
    pickle.dump(test_videos, f, protocol=pickle.HIGHEST_PROTOCOL)

## Use structure.pkl file

In [4]:
train_videos = pickle.load(open("train_structure.pkl", "rb"))
test_videos = pickle.load(open("test_structure.pkl", "rb"))


## Video example

In [5]:
class_name = "Explosion"
video_name = "Explosion030"
video_info = train_videos[class_name][video_name]
frames_list = video_info["frames"]
mpl.rcParams['animation.embed_limit'] = 100  

images = []
for p in frames_list:
    with Image.open(p) as img:
        images.append(img.copy())
        

fig, ax = plt.subplots(figsize=(4, 4))
ax.axis('off')

def anim(i):
    ax.clear(); ax.axis('off'); ax.imshow(images[i])

ani = FuncAnimation(fig, anim, frames=len(images), interval=40, repeat=True)
plt.close(fig)
HTML(ani.to_jshtml())